In [2]:
import requests
from bs4 import BeautifulSoup
import re
import json

In [191]:
def get_more_button_links(url):
    more_authors_links = []
    res = requests.get(url)
    soup = BeautifulSoup(res.content, 'lxml')
    div_tags = soup.find_all('div' , class_='bq_fl indexContent authorContent')
    for div_tag in div_tags:
        link_div_tag = div_tag.select_one('[style="padding-top:5px"]')
        link = "https://www.brainyquote.com"+link_div_tag.a['href']
        more_authors_links.append(link)
    return more_authors_links

def get_urls_of_authors_quotes(more_authors_links):
    urls_of_authors_quotes = []
    for more_author_link in more_authors_links:
        no_of_pages = find_no_of_pages_for_each_author(more_author_link)
        urls = get_urls_for_each_author_page(no_of_pages,more_author_link)
        for url in urls:
            res = requests.get(url)
            soup = BeautifulSoup(res.content, 'lxml')
            table_tag = soup.find('tbody')
            tr_tags = table_tag.find_all('tr')
            for tr_tag in tr_tags:
                td_tag = tr_tag.find('td')
                link = "https://www.brainyquote.com"+td_tag.a['href']
                urls_of_authors_quotes.append(link)
    return urls_of_authors_quotes


def extract_quotes_from_each_author_url(author_quotes_urls):
    for author_quote_url in author_quotes_urls:
        no_of_author_quotes_pages = find_no_of_pages_for_each_author_quotes(author_quote_url)
        quotes_urls = get_urls_for_each_authore_quotes_pages(no_of_author_quotes_pages,author_quote_url)
        for quote_url in  quotes_urls:
            res = requests.get(quote_url)
            soup = BeautifulSoup(res.content, 'lxml')
            quotes_div_tag = soup.find('div', id='qbcc')
            quotes_cards_tag = quotes_div_tag.find_all('div', class_='grid-item qb clearfix bqQt')
            for card_tag in quotes_cards_tag :
                each_quote_link = "https://www.brainyquote.com"+card_tag.a['href']
                response = requests.get(each_quote_link)
                soup1 = BeautifulSoup(response.content, 'lxml')
                author_name = soup1.find('p', class_= 'bq_fq_a').text.replace('\n','')
                quote_paragrapgh = soup1.find('p').text.replace('\n','')
                info_tags= soup1.find_all('div', class_='bq_fl')
                modify_data(author_name,quote_paragrapgh,info_tags)


def modify_data(author_name,quote,info_tags):
    deials = " "
    #print(info_tags)
    print("Author Name: "+author_name)
    f.write("Author Name: "+author_name+"\n")
    if(len(info_tags)==4):
        details = info_tags[2].text.replace('\n',' ')
    elif(len(info_tags)==3):
        details = info_tags[1].text.replace('\n',' ')
    try:
        x = details.split("-")
        if(len(x)==2  and (not "Born:" in details)):
            without_birth_death_date(x,quote,info_tags)
        else:
            y = x[1].split("  ", 1)
            if "Born: " in details:
                without_date_of_death(y)
            else:
                all_personal_data_availaible(x,y)
            
            print("Nationality:"+x[0])
            f.write("Nationality:"+x[0]+"\n")
            print("Occupation:"+y[0] )
            f.write("Occupation:"+y[0]+"\n")
            print("Quote:"+quote)
            f.write("Quote:"+quote+"\n")
            print("Related Tags:"+info_tags[0].text.replace('\n',' '))
            f.write("Related Tags:"+info_tags[0].text.replace('\n',' ')+"\n")
            print(" ")
            f.write("\n")
            
    except:
        no_personal_data_available(quote,info_tags)
        
def all_personal_data_availaible(x,y):
    print("Born:"+y[1])
    f.write("Born:"+y[1]+"\n")
    print("Death:"+x[2])
    f.write("Death:"+x[2]+"\n")
    
def without_date_of_death(y):
    print(y[1])
    f.write(y[1]+"\n")
    
def without_birth_death_date(x,quote,info_tags):
    print("Nationality:"+x[0])
    f.write("Nationality:"+x[0]+"\n")
    print("Occupation:"+x[1] )
    f.write("Occupation:"+x[1]+"\n")
    print("Quote:"+quote)
    f.write("Quote:"+quote+"\n")
    print("Related Tags:"+info_tags[0].text.replace('\n',' '))
    f.write("Related Tags:"+info_tags[0].text.replace('\n',' ')+"\n")
    print(" ")
    f.write("\n")
    
def no_personal_data_available(quote,info_tags):
    print("Quote:"+quote)
    f.write("Quote:"+quote+"\n")
    print("Related Tags:"+info_tags[0].text.replace('\n',' '))
    f.write("Related Tags:"+info_tags[0].text.replace('\n',' ')+"\n")
    print(" ")
    f.write("\n")



def get_urls_for_each_authore_quotes_pages(no_of_author_quotes_pages,url):
    quotes_urls = []
    for i in range(1,no_of_author_quotes_pages+1):
        link = url+"_"+str(i)
        quotes_urls.append(link)
    return quotes_urls


def get_urls_for_each_author_page(no_of_pages,url):
    urls = []
    for i in range(1,no_of_pages+1):
        link = url+str(i)
        urls.append(link)
    return urls

    
def find_no_of_pages_for_each_author(url):
    no_of_pages = 1
    try:
        res = requests.get(url)
        soup = BeautifulSoup(res.content, 'lxml')
        pagination_tag = soup.find('ul' , class_='pagination bqNPgn pagination-sm')
        li_tags =  pagination_tag.find_all('li')
        for li_tag in li_tags:
            text = li_tag.text.replace('\n', '')
            if(text == "Next" or text == "Prev" or text == ".."):
                continue
            else:
                if(int(text)> no_of_pages):
                    no_of_pages = int(text)
        return no_of_pages
    except:
        return no_of_pages
    

def find_no_of_pages_for_each_author_quotes(url):
    no_of_quotes_pages = 1
    try:
        res = requests.get(url)
        soup = BeautifulSoup(res.content, 'lxml')
        pagination_tag = soup.find('ul' , class_='pagination bq_pageNumbers pagination-centered pagination-sm')
        li_tags =  pagination_tag.find_all('li')
        for li_tag in li_tags:
            text = li_tag.text.replace('\n', '')
            if(text == "Next" or text == "Prev" or text == ".."):
                continue
            else:
                if(int(text)> no_of_quotes_pages):
                    no_of_quotes_pages = int(text)
        return no_of_quotes_pages
    except:
        return no_of_quotes_pages
    
    
    
#main function
if __name__ == '__main__':
    global f
    f=open('brain_quotes.txt','w') 
    more_authors_links = get_more_button_links('https://www.brainyquote.com/authors')
    author_quotes_urls = get_urls_of_authors_quotes(more_authors_links)
    extract_quotes_from_each_author_url(author_quotes_urls)
    f.close()

Author Name: A Boogie wit da Hoodie
Born: December 6, 1995 
Nationality: American 
Occupation: Musician
Quote:I can't even lie: Sometimes, I be antisocial.
Related Tags: Bob Dylan, Willie Nelson, Lil Baby, LL Cool J, Jimi Hendrix, Doja Cat, Tom Waits, Cher 
 
Author Name: A Boogie wit da Hoodie
Born: December 6, 1995 
Nationality: American 
Occupation: Musician
Quote:Everything I do is me. I don't like taking ideas from people unless they're the G.O.A.T.
Related Tags: Taking, Unless 
 
Author Name: A Boogie wit da Hoodie
Born: December 6, 1995 
Nationality: American 
Occupation: Musician
Quote:Being self-made means putting yourself in position to help others put themselves in position to be successful.
Related Tags: Being, Help Others, Means, Others, Putting, Successful, Themselves 
 
Author Name: A Boogie wit da Hoodie
Born: December 6, 1995 
Nationality: American 
Occupation: Musician
Quote:Perfecting your craft is one of the main keys in being successful.
Related Tags: Keys 
 
Autho

Author Name: A Boogie wit da Hoodie
Born: December 6, 1995 
Nationality: American 
Occupation: Musician
Quote:People's hustle in the Bronx is real.
Related Tags: Bob Dylan, Willie Nelson, Lil Baby, LL Cool J, Jimi Hendrix, Doja Cat, Tom Waits, Cher 
 
Author Name: A Boogie wit da Hoodie
Born: December 6, 1995 
Nationality: American 
Occupation: Musician
Quote:Every time I step on stage an' see all of the lights or hear fans singing the words to my songs ,it's a surreal moment for me.
Related Tags: Every, Every Time, Hear, Lights, See, Singing, Songs, Stage, Surreal, Words 
 
Author Name: A Boogie wit da Hoodie
Born: December 6, 1995 
Nationality: American 
Occupation: Musician
Quote:Hip-hop originated from the Bronx specifically; that means everything. I'm down the block from where hip-hop was born and raised, so I'm glad I am here and I'm able to represent New York the way I am.
Related Tags: Able, Am, Block, Bronx, Down, Everything, Glad, Here, Means, New York, Originated, Raised, Re

Author Name: A Boogie wit da Hoodie
Born: December 6, 1995 
Nationality: American 
Occupation: Musician
Quote:Some of my songs are turnt up, but that's just 'cause I have to make 'em like that so the clubs can play them.
Related Tags: Cause, Clubs, Some, Songs, Them 
 
Author Name: A Boogie wit da Hoodie
Born: December 6, 1995 
Nationality: American 
Occupation: Musician
Quote:Not everyone's really got the heart to talk about what's going on with their love in their music.
Related Tags: About, Going, Got, Really 
 
Author Name: A Boogie wit da Hoodie
Born: December 6, 1995 
Nationality: American 
Occupation: Musician
Quote:I overloaded myself with work. I give myself work to do so I don't give myself time to chill and have free time to chill with the family as much.
Related Tags: Chill, Free Time, Give, Much 
 
Author Name: A Boogie wit da Hoodie
Born: December 6, 1995 
Nationality: American 
Occupation: Musician
Quote:I had to realize that you can't try to get money, support yourself,

Author Name: A'Lelia Bundles
Born: June 7, 1952 
Nationality: American 
Occupation: Journalist
Quote:We buy too much stuff we just don't need. We're trying to look cute for next weekend when we ought to be thinking about the next decade.
Related Tags: About, Buy, Decade, Just, Much, Need, Next, Ought, Stuff, Too, Weekend 
 
Author Name: A'Lelia Bundles
Born: June 7, 1952 
Nationality: American 
Occupation: Journalist
Quote:God puts pack rats together with non-pack rats.
Related Tags: Andy Rooney, Hunter S. Thompson, Erma Bombeck, Fran Lebowitz, Ambrose Bierce, Ann Landers, Dave Barry, Sydney J. Harris 
 
Author Name: A'Lelia Bundles
Born: June 7, 1952 
Nationality: American 
Occupation: Journalist
Quote:I have lived almost seven decades. So I've had my hair journey where I wasn't comfortable with my hair.
Related Tags: Almost, Decades, Had, Seven 
 
Author Name: A'Lelia Bundles
Born: June 7, 1952 
Nationality: American 
Occupation: Journalist
Quote:A'Lelia Walker did not subsidize spec

Author Name: A'Lelia Bundles
Born: June 7, 1952 
Nationality: American 
Occupation: Journalist
Quote:Don't sit around and wait for the opportunities to come. You have to get up and make those opportunities come.
Related Tags: Around, Get, Opportunities, Those, You 
 
Author Name: A'Lelia Bundles
Born: June 7, 1952 
Nationality: American 
Occupation: Journalist
Quote:There are schools that have rules against afro puffs. They say it's distracting. But nobody is saying that about a little girl who has ponytails.
Related Tags: About, Against, Distracting, Little, Little Girl, Saying, Schools, Who 
 
Author Name: A'Lelia Bundles
Born: June 7, 1952 
Nationality: American 
Occupation: Journalist
Quote:So Madam C.J. Walker's Wonderful Hair Grower, when applied after shampooing the hair more frequently, allowed women's scalp to be healthier and their hair to grow back. That was her most popular product.
Related Tags: After, Allowed, Applied, Frequently, Healthier, Her, Madam, More, Most, Popula

...

Author Name: Aerin Lauder
Born: April 23, 1970 
Nationality: American 
Occupation: Businesswoman
Quote:I love laugh lines. It means you've had a good life. The most beautiful women - Audrey Hepburn, Lauren Hutton, Ali MacGraw - all embraced the aging process.
Related Tags: Aging, Ali, Beautiful, Beautiful Women, Embraced, Good Life, Had, I Love, Laugh, Lauren, Lines, Means, Most, Process, You 
 
Author Name: Aerin Lauder
Born: April 23, 1970 
Nationality: American 
Occupation: Businesswoman
Quote:I usually keep my personal style simple and streamlined. I like classic colors like black, white, and beige. White and black is my favorite color combination, and I like to finish up my look with an accent of gold jewelry.
Related Tags: Accent, Classic, Color, Combination, Favorite, Finish, Jewelry, Keep, Like, Personal, Personal Style, Simple, Up, White 
 
Author Name: Aerin Lauder
Born: April 23, 1970 
Nationality: American 
Occupation: Businesswoman
Quote:I like to entertain at home, to liv

Author Name: Aerin Lauder
Born: April 23, 1970 
Nationality: American 
Occupation: Businesswoman
Quote:In terms of pots and pans, I just use the basics - I'm not a snob like that.
Related Tags: Pots, Terms 
 
Author Name: Aerin Lauder
Born: April 23, 1970 
Nationality: American 
Occupation: Businesswoman
Quote:You can't be a major company today without paying attention to celebrities. They are the leaders in beauty and fashion.
Related Tags: Attention, Celebrities, Leaders, Major, Paying, You 
 
Author Name: Aerin Lauder
Born: April 23, 1970 
Nationality: American 
Occupation: Businesswoman
Quote:I used to be a shopper before I had children. I'd go to Bergdorf and Barneys all the time. But now my weekends are spent differently. I go to the skating rink or the park, not the stores.
Related Tags: Before, Differently, Had, Park, Rink, Spent, Stores, Used, Weekends 
 
Author Name: Aerin Lauder
Born: April 23, 1970 
Nationality: American 
Occupation: Businesswoman
Quote:Growing up in New Yo

Author Name: Aerin Lauder
Born: April 23, 1970 
Nationality: American 
Occupation: Businesswoman
Quote:Estee Lauder was my grandmother. She was an iconic and powerful woman, but to us, she was just Estee. She was the first person to teach me how important it is to be passionate and proud of what you do, and always talked about 'balance.'
Related Tags: About, Always, First, First-Person, Grandmother, How, Iconic, Just, Passionate, Proud, She, Talked, Teach, Us, Woman, You 
 
Author Name: Aerin Lauder
Born: April 23, 1970 
Nationality: American 
Occupation: Businesswoman
Quote:I love Pilates, I really do, and I do it three times a week because it works well for me.
Related Tags: Because, I Love, Pilates, Really, Times, Works 
 
Author Name: Aerin Lauder
Born: April 23, 1970 
Nationality: American 
Occupation: Businesswoman
Quote:When we moved to Europe when I was a teenager, I really did not want to go. I was happy in my school, with my friends, but looking back on it, it was the best ex

Author Name: Aeschylus
Born:525 BC 
Death: 456 BC 
Nationality: Greek 
Occupation: Poet
Quote:Excessive fear is always powerless.
Related Tags: Powerless 
 
Author Name: Aeschylus
Born:525 BC 
Death: 456 BC 
Nationality: Greek 
Occupation: Poet
Quote:God loves to help him who strives to help himself.
Related Tags: Him, Loves 
 
Author Name: Aeschylus
Born:525 BC 
Death: 456 BC 
Nationality: Greek 
Occupation: Poet
Quote:Of all the gods only death does not desire gifts.
Related Tags: Does 
 
Author Name: Aeschylus
Born:525 BC 
Death: 456 BC 
Nationality: Greek 
Occupation: Poet
Quote:Everyone's quick to blame the alien.
Related Tags: Sophocles, Euripides, Homer, Menander, Hesiod, Aristophanes, Pindar, Archilochus 
 
Author Name: Aeschylus
Born:525 BC 
Death: 456 BC 
Nationality: Greek 
Occupation: Poet
Quote:Death is softer by far than tyranny.
Related Tags: Sophocles, Euripides, Homer, Menander, Hesiod, Aristophanes, Pindar, Archilochus 
 
Author Name: Aeschylus
Born:525 BC 
Death: 456

ReadTimeout: HTTPSConnectionPool(host='www.brainyquote.com', port=443): Read timed out. (read timeout=None)

In [ ]:
American - Musician  Born: December 6, 1995 
Polish - Sociologist  November 19, 1925 - January 9, 2017 
[' Polish ', ' Sociologist  November 19, 1925 ', ' January 9, 2017 ']
[' American ', ' Musician  Born: December 6, 1995 ']